In [1]:
import numpy as np
import os
import csv
import igl
import math
import matplotlib.pyplot as plt
import mpl_toolkits.mplot3d 
import geopandas as gpd
import plotly.graph_objects as go
import ripleyK as rk

In [60]:
#Spatio-temporal analysis
current_dir = os.getcwd()
folder_path = os.path.join(current_dir, "Whale_spatio_temporal")

path = os.path.join(folder_path, "Blue and fin whales Southern California 2014-2015 - Argos data.csv")
with open(path, 'r') as file:
    csvreader = csv.reader(file)
    data = []
    for row in csvreader:
        data.append(row)
    data = np.array(data)

print(data.shape)

(4283, 28)


In [63]:
# read all csv files in the folder
data = np.empty((0, 5))
for file_name in os.listdir(folder_path):
    if file_name.endswith(".csv"):
        file_path = os.path.join(folder_path, file_name)
        print(file_path)
        with open(file_path, 'r') as file:
            csvreader = csv.reader(file)
            for row in csvreader:
                # Append the row to the data array, skipping the header row
                if csvreader.line_num > 1:
                    temp = np.array(row)
                    # slice first 5 columns from temp
                    temp = temp[:5]
                    data = np.vstack((data, np.array(temp)))



c:\Users\muhan\Documents\Datalogi\bachelor\Bachelor-project\Code\Whale_spatio_temporal\Antarctic blue whales, east Antarctic sector of the Southern Ocean.csv
c:\Users\muhan\Documents\Datalogi\bachelor\Bachelor-project\Code\Whale_spatio_temporal\Blue and fin whales Southern California 2014-2015 - Argos data.csv
c:\Users\muhan\Documents\Datalogi\bachelor\Bachelor-project\Code\Whale_spatio_temporal\Blue whales Eastern North Pacific 2003 State-space model output.csv
c:\Users\muhan\Documents\Datalogi\bachelor\Bachelor-project\Code\Whale_spatio_temporal\Bowhead whale Admiralty Inlet.csv
c:\Users\muhan\Documents\Datalogi\bachelor\Bachelor-project\Code\Whale_spatio_temporal\False Killer Whales - Hawaiian Islands- PIFSC.csv
c:\Users\muhan\Documents\Datalogi\bachelor\Bachelor-project\Code\Whale_spatio_temporal\Sperm whale CRC NW Atlantic.csv
c:\Users\muhan\Documents\Datalogi\bachelor\Bachelor-project\Code\Whale_spatio_temporal\Sperm whales Gulf of Mexico 2011-2013 ADB Tags - Argos data.csv
c:\Us

In [67]:
print(data.shape)
# output the data to csv file
data = np.array(data)
result_path = os.path.join(current_dir, "whale_spatio_temporal.csv")
np.savetxt(result_path, data, delimiter=",", header='id,visible,time,lon,lat', fmt='%s')

(19307, 5)


In [65]:
time = data[1:,2]
long = data[1:,3]
lat = data[1:,4]

stpp = np.column_stack((time, long, lat))

# remove rows with long or lat = ''
stpp= stpp[stpp[:,1] != '']

# convert to polar coordinates
long = np.array(stpp[:,1], dtype=float)
lat = np.array(stpp[:,2], dtype=float)

def longConvert(long):
    for i in range(len(long)):
        if long[i] < 0:
            long[i] = 360 + long[i]
    return long

lat = 90 - lat # north pole is 90, south pole is -90, convert to 0 to 180
long = longConvert(long) # convert to 0 to 360

# convert to radians
long = np.deg2rad(long)
lat = np.deg2rad(lat)
# convert to cartesian coordinates
r = 1
x = r*np.cos(long)*np.sin(lat)
y = r*np.sin(long)*np.sin(lat)
z = r*np.cos(lat)

stpp = np.column_stack((stpp[:,0], x, y, z))

In [66]:
vertices, faces = igl.read_triangle_mesh(os.path.join(current_dir, "mesh", "ocean_mesh_500_simplified.obj"))

vx, vy, vz = vertices.T
fi, fj, fk = faces.T
# points_uniform = sample_faces(vertices, faces, 100)

mesh = go.Mesh3d(x=vx, y=vy, z=vz, i=fi, j=fj, k=fk, color='blue', opacity=0.3)
samples_whale = go.Scatter3d(x=x, y=y, z=z, mode='markers', marker=dict(size=2, color='black'), name='Whale locations')
# samples_uniform = go.Scatter3d(x=points_uniform[:, 0], y=points_uniform[:, 1], z=points_uniform[:, 2], mode='markers', marker=dict(size=2, color='red'), name='Uniform samples')

fig = go.Figure(data=[mesh, samples_whale])
fig.show()